## This notebook will process all of the data in the antenna result directories and produce a 'processed_data.csv' file.

#### The below cell will install dependencies, if needed.

In [20]:
# %%capture
# ! pip install folium
# ! pip install pandas
# ! pip install pandas_profiling

Traceback (most recent call last):
  File "C:\Users\steve\Anaconda3\Scripts\jupyter-nbextension-script.py", line 10, in <module>
    sys.exit(main())
  File "C:\Users\steve\Anaconda3\lib\site-packages\jupyter_core\application.py", line 266, in launch_instance
    return super(JupyterApp, cls).launch_instance(argv=argv, **kwargs)
  File "C:\Users\steve\Anaconda3\lib\site-packages\traitlets\config\application.py", line 658, in launch_instance
    app.start()
  File "C:\Users\steve\Anaconda3\lib\site-packages\notebook\nbextensions.py", line 988, in start
    super(NBExtensionApp, self).start()
  File "C:\Users\steve\Anaconda3\lib\site-packages\jupyter_core\application.py", line 255, in start
    self.subapp.start()
  File "C:\Users\steve\Anaconda3\lib\site-packages\notebook\nbextensions.py", line 716, in start
    self.install_extensions()
  File "C:\Users\steve\Anaconda3\lib\site-packages\notebook\nbextensions.py", line 695, in install_extensions
    **kwargs
  File "C:\Users\steve\Anaco

#### The necessary dependencies are imported.

In [11]:
import pandas as pd
import pandas_profiling
import folium
from folium.plugins import HeatMap
from IPython.core.display import display, HTML
import base64

#### Add values for the below variables to return a processed file containing only a subset of the data.
##### For example, add a species to return a file of only data for that species. Or, add a species and an antenna to get data for a specific species/antenna

In [12]:
# User Selections
# Add a pythonic list to any of these for getting a subset of the data for the below analytics functions.
# This will not overwrite the processed_data.csv file with the subset.

SPECIES = []
ANTENNA = []
DATE = []
TAGID = []
COLUMNS = []

#### Execute 'fish_data.py' processing script. This creates the 'processed_data.csv' file. Each time this cell is run it will recreate the 'processed_data.csv' file.

In [ ]:
%run -i fish_data

#### The cell below does all of the heavy lifting of reading the 'processed_data.csv' file into a dataframe for use in the operations below.

In [13]:
# prepare dataframe for analysis

# Load antenna data into a dataframe
data = pd.read_csv('./processed_data.csv', low_memory=False)

print(data.sample())
print(data.shape)

      D        Date      Time     Duration Type          Tag ID  Count Gap  \
9474  D  2018-06-21  17:00:00  00:00:01.02   HA  3D6.00184CBA07      2  44   

     Antenna        Lat       Long Species  Length Marked At  Week  D1  U1  \
9474      D1  33.998528 -84.894528    LEAU      75      D1.0    25   1   0   

      U2  U3  
9474   0   0  
(30034, 19)


#### The below cell creates the subset dataframe from the selection provided by the user above. It will perform the heatmapping and the pandas_profiling from this subset. 

In [ ]:
# Create a data subset, if desired.

if SPECIES:
    data = data.loc[data['Species'].isin(SPECIES)]
if ANTENNA:
    data = data.loc[data['Antenna'].isin(ANTENNA)]
if DATE:
    data = data.loc[data_subset['Date'].isin(DATE)]
if TAGID:
    data = data.loc[data_subset['Tag ID'].isin(TAGID)]
if COLUMNS:
    data = data.filter(COLUMNS, axis=1)

In [ ]:
pandas_profiling.ProfileReport(data)

In [ ]:
fishTrackMap = folium.Map(location=[33.99697222, -84.89694444], zoom_start=15) 

# Ensure floats
data['lat'] = data['lat'].astype(float)
data['lat'] = data['lat'].astype(float)

# Remove NaNs
data = data[['lat', 'long']]
data = data.dropna(axis=0, subset=['lat','long'])

# List comprehension to make out list of lists
heat_data = [[row['lat'],row['long']] for index, row in data.iterrows()]

# Plot it on the map
HeatMap(heat_data).add_to(fishTrackMap)

# Display the map
fishTrackMap



#### Create a 'facets' dive to visually explore the data using the left side tool bar.

In [14]:
df = data
jsonstr = df.to_json(orient='records')

HTML_TEMPLATE = \
    """
        <link rel="import" href="/nbextensions/facets-dist/facets-jupyter.html">
        <facets-dive id="elem_id" height="600"></facets-dive>
        <script>
          var data = {jsonstr};
          document.querySelector("#elem_id").data = data;
        </script>
    """
html = HTML_TEMPLATE.format(jsonstr=jsonstr)
display(HTML(html))